In [1]:
import sys
import time
sys.path.insert(0, '/home/anish/ASC_ML')

In [2]:
from ASC_ML import multiple_model_gen_v2 as multiple
from ASC_ML import dataframe_extractor as de
from ASC_ML import model_generation as model_gen
# from ASC_ML import model_gen_train_test as testing
from dask_ml.preprocessing import LabelEncoder
# from dask_ml.preprocessing import MinMaxScaler
from sklearn.preprocessing import MinMaxScaler

2022-07-03 10:01:47.298004: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcudart.so.10.1


In [3]:
# m = multiple.Multiple_Model_Gen(max_no_layers = 2, model_per_batch = 10)

In [4]:
# import dask.dataframe as dd
# import pandas as pd
# data = dd.from_pandas(pd.Series(['a', 'a', 'b'], dtype='category'),
#                      npartitions=1)
# le = LabelEncoder()
# le.fit_transform(data).compute()
# print(type(le.fit_transform(data).compute()))

In [5]:
#For House Prediction Dataset https://www.kaggle.com/c/house-prices-advanced-regression-techniques/data?select=train.csv
directory1 = "/home/anish/ASC-ML-EXP-DATASETS/LinReg-tabular/house-prices-advanced-regression-techniques/train.csv"


# returns list of dask dataframe [singular_df_x, singular_df_y] or [train_df_x, train_df_y, test_df_x, test_df_y]
dataset_list = de.DataframeExtractor_csv(directory1, label_names = ["SalePrice"]).df_list

print("Train Dataset X Columns")
dataset_list[0].head()

Reading single csv from /home/anish/ASC-ML-EXP-DATASETS/LinReg-tabular/house-prices-advanced-regression-techniques/train.csv
Train Dataset X Columns


Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0  1.0        60.0       RL         65.0   8450.0   Pave   NaN      Reg   
1  2.0        20.0       RL         80.0   9600.0   Pave   NaN      Reg   
2  3.0        60.0       RL         68.0  11250.0   Pave   NaN      IR1   
3  4.0        70.0       RL         60.0   9550.0   Pave   NaN      IR1   
4  5.0        60.0       RL         84.0  14260.0   Pave   NaN      IR1   

  LandContour Utilities  ... ScreenPorch PoolArea PoolQC Fence MiscFeature  \
0         Lvl    AllPub  ...         0.0      0.0    NaN   NaN         NaN   
1         Lvl    AllPub  ...         0.0      0.0    NaN   NaN         NaN   
2         Lvl    AllPub  ...         0.0      0.0    NaN   NaN         NaN   
3         Lvl    AllPub  ...         0.0      0.0    NaN   NaN         NaN   
4         Lvl    AllPub  ...         0.0      0.0    NaN   NaN         NaN   

  MiscVal MoSold  YrSold  SaleType  SaleCondition  
0     0.0    2.0  2008.0        WD         Normal  
1     0.0    5.0  2007.0        WD         Normal  
2     0.0    9.0  2008.0        WD         Normal  
3     0.0    2.0  2006.0        WD        Abnorml  
4     0.0   12.0  2008.0        WD         Normal  

[5 rows x 80 columns]

In [6]:
dataset_list[1].head()

SalePrice
0   208500.0
1   181500.0
2   223500.0
3   140000.0
4   250000.0

In [7]:
train_x = dataset_list[0].copy()

In [8]:
train_x = train_x.fillna(0)

In [9]:
train_x.head()

Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0  1.0        60.0       RL         65.0   8450.0   Pave     0      Reg   
1  2.0        20.0       RL         80.0   9600.0   Pave     0      Reg   
2  3.0        60.0       RL         68.0  11250.0   Pave     0      IR1   
3  4.0        70.0       RL         60.0   9550.0   Pave     0      IR1   
4  5.0        60.0       RL         84.0  14260.0   Pave     0      IR1   

  LandContour Utilities  ... ScreenPorch PoolArea PoolQC Fence MiscFeature  \
0         Lvl    AllPub  ...         0.0      0.0      0     0           0   
1         Lvl    AllPub  ...         0.0      0.0      0     0           0   
2         Lvl    AllPub  ...         0.0      0.0      0     0           0   
3         Lvl    AllPub  ...         0.0      0.0      0     0           0   
4         Lvl    AllPub  ...         0.0      0.0      0     0           0   

  MiscVal MoSold  YrSold  SaleType  SaleCondition  
0     0.0    2.0  2008.0        WD         Normal  
1     0.0    5.0  2007.0        WD         Normal  
2     0.0    9.0  2008.0        WD         Normal  
3     0.0    2.0  2006.0        WD        Abnorml  
4     0.0   12.0  2008.0        WD         Normal  

[5 rows x 80 columns]

In [10]:
train_x['MSSubClass'] = train_x['MSSubClass'].apply(str)

train_x['OverallCond'] = train_x['OverallCond'].astype(str)

train_x['YrSold'] = train_x['YrSold'].astype(str)
train_x['MoSold'] = train_x['MoSold'].astype(str)
train_x.head()

/home/anish/anaconda3/envs/tfgpu/lib/python3.9/site-packages/dask/dataframe/core.py:3946: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=('MSSubClass', 'object'))

  warnings.warn(meta_warning(meta))


Id MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0  1.0       60.0       RL         65.0   8450.0   Pave     0      Reg   
1  2.0       20.0       RL         80.0   9600.0   Pave     0      Reg   
2  3.0       60.0       RL         68.0  11250.0   Pave     0      IR1   
3  4.0       70.0       RL         60.0   9550.0   Pave     0      IR1   
4  5.0       60.0       RL         84.0  14260.0   Pave     0      IR1   

  LandContour Utilities  ... ScreenPorch PoolArea PoolQC Fence MiscFeature  \
0         Lvl    AllPub  ...         0.0      0.0      0     0           0   
1         Lvl    AllPub  ...         0.0      0.0      0     0           0   
2         Lvl    AllPub  ...         0.0      0.0      0     0           0   
3         Lvl    AllPub  ...         0.0      0.0      0     0           0   
4         Lvl    AllPub  ...         0.0      0.0      0     0           0   

  MiscVal MoSold  YrSold SaleType  SaleCondition  
0     0.0    2.0  2008.0       WD         Normal  
1     0.0    5.0  2007.0       WD         Normal  
2     0.0    9.0  2008.0       WD         Normal  
3     0.0    2.0  2006.0       WD        Abnorml  
4     0.0   12.0  2008.0       WD         Normal  

[5 rows x 80 columns]

In [11]:
# a = train_x['LotShape']

In [12]:
# le = LabelEncoder() 
# le.fit_transform(a).compute()
# train_x['LotShape'] = le.fit_transform(train_x['LotShape'])

In [13]:
# train_x.head()

In [14]:
def keyval(allkeys):
    i = 0
    keyvalpairs = list()
    for key in allkeys:
        keyvalpairs.append((key,i))
        i+=1
    return dict(keyvalpairs)

In [15]:
# cols = ['FireplaceQu', 'LotShape']
cols = ['FireplaceQu', 'BsmtQual', 'BsmtCond', 'GarageQual', 'GarageCond', 
        'ExterQual', 'ExterCond','HeatingQC', 'PoolQC', 'KitchenQual', 'BsmtFinType1', 
        'BsmtFinType2', 'Functional', 'Fence', 'BsmtExposure', 'GarageFinish', 'LandSlope',
        'LotShape', 'PavedDrive', 'Street', 'Alley', 'CentralAir', 'MSSubClass', 'OverallCond', 
        'YrSold', 'MoSold']
keys = {}
for col in cols:
    key = train_x[col].unique()
    keyvalpairs = keyval(key)
    keys.update({col:keyvalpairs})


In [16]:
keys

{'FireplaceQu': {0: 0, 'TA': 1, 'Gd': 2, 'Fa': 3, 'Ex': 4, 'Po': 5},
 'BsmtQual': {'Gd': 0, 'TA': 1, 'Ex': 2, 0: 3, 'Fa': 4},
 'BsmtCond': {'TA': 0, 'Gd': 1, 0: 2, 'Fa': 3, 'Po': 4},
 'GarageQual': {'TA': 0, 'Fa': 1, 'Gd': 2, 0: 3, 'Ex': 4, 'Po': 5},
 'GarageCond': {'TA': 0, 'Fa': 1, 0: 2, 'Gd': 3, 'Po': 4, 'Ex': 5},
 'ExterQual': {'Gd': 0, 'TA': 1, 'Ex': 2, 'Fa': 3},
 'ExterCond': {'TA': 0, 'Gd': 1, 'Fa': 2, 'Po': 3, 'Ex': 4},
 'HeatingQC': {'Ex': 0, 'Gd': 1, 'TA': 2, 'Fa': 3, 'Po': 4},
 'PoolQC': {0: 0, 'Ex': 1, 'Fa': 2, 'Gd': 3},
 'KitchenQual': {'Gd': 0, 'TA': 1, 'Ex': 2, 'Fa': 3},
 'BsmtFinType1': {'GLQ': 0,
  'ALQ': 1,
  'Unf': 2,
  'Rec': 3,
  'BLQ': 4,
  0: 5,
  'LwQ': 6},
 'BsmtFinType2': {'Unf': 0,
  'BLQ': 1,
  0: 2,
  'ALQ': 3,
  'Rec': 4,
  'LwQ': 5,
  'GLQ': 6},
 'Functional': {'Typ': 0,
  'Min1': 1,
  'Maj1': 2,
  'Min2': 3,
  'Mod': 4,
  'Maj2': 5,
  'Sev': 6},
 'Fence': {0: 0, 'MnPrv': 1, 'GdWo': 2, 'GdPrv': 3, 'MnWw': 4},
 'BsmtExposure': {'No': 0, 'Gd': 1, 'Mn': 2, '

In [17]:
train_X = train_x.replace(keys).copy()

In [18]:
train_X['FireplaceQu'].unique().compute()

0    0
1    1
2    2
3    3
4    4
5    5
Name: FireplaceQu, dtype: int64

In [19]:
train_X.head()

Id  MSSubClass MSZoning  LotFrontage  LotArea  Street  Alley  LotShape  \
0  1.0           0       RL         65.0   8450.0       0      0         0   
1  2.0           1       RL         80.0   9600.0       0      0         0   
2  3.0           0       RL         68.0  11250.0       0      0         1   
3  4.0           2       RL         60.0   9550.0       0      0         1   
4  5.0           0       RL         84.0  14260.0       0      0         1   

  LandContour Utilities  ... ScreenPorch  PoolArea PoolQC Fence MiscFeature  \
0         Lvl    AllPub  ...         0.0       0.0      0     0           0   
1         Lvl    AllPub  ...         0.0       0.0      0     0           0   
2         Lvl    AllPub  ...         0.0       0.0      0     0           0   
3         Lvl    AllPub  ...         0.0       0.0      0     0           0   
4         Lvl    AllPub  ...         0.0       0.0      0     0           0   

  MiscVal MoSold  YrSold  SaleType  SaleCondition  
0     0.0      0       0        WD         Normal  
1     0.0      1       1        WD         Normal  
2     0.0      2       0        WD         Normal  
3     0.0      0       2        WD        Abnorml  
4     0.0      3       0        WD         Normal  

[5 rows x 80 columns]

In [20]:
cols_to_remove = []
for col in train_X.columns:
#     print(type(col))
    try:
        a = train_X[col].astype(float).compute()
    except ValueError:
#         print('Couldn\'t covert %s to float' % col)
        cols_to_remove.append(col)
        pass

# keep only the columns in df that do not contain string
train_X = train_X[[col for col in train_X.columns if col not in cols_to_remove]]

In [21]:
print(cols_to_remove)

['MSZoning', 'LandContour', 'Utilities', 'LotConfig', 'Neighborhood', 'Condition1', 'Condition2', 'BldgType', 'HouseStyle', 'RoofStyle', 'RoofMatl', 'Exterior1st', 'Exterior2nd', 'MasVnrType', 'Foundation', 'Heating', 'Electrical', 'GarageType', 'MiscFeature', 'SaleType', 'SaleCondition']


In [22]:
train_X = train_X.drop(["Id"], axis = 1)

In [23]:
# tsklearn.preprocessing.MinMaxScalerrain_X.head()

In [24]:
len(train_X.columns)

58

In [25]:
len(dataset_list[1].columns)

1

In [26]:
scaler_x = MinMaxScaler()
scaler_x.fit(train_X)
train_X_scaled = scaler_x.transform(train_X)

scaler_y = MinMaxScaler()
scaler_y.fit(dataset_list[1])
train_Y_scaled = scaler_y.transform(dataset_list[1])

In [27]:
# col = train_X.columns.to_list()
# scaler_d = MinMaxScaler()
# train_X.columns = list(train_X.columns)
# scaled_train_X = scaler_d.fit_transform(train_X[col])

In [28]:
train_X_scaled
# train_Y_scaled

array([[0.        , 0.20766773, 0.0334198 , ..., 0.        , 0.        ,
        0.        ],
       [0.07142857, 0.25559105, 0.03879502, ..., 0.        , 0.09090909,
        0.25      ],
       [0.        , 0.2172524 , 0.04650728, ..., 0.        , 0.18181818,
        0.        ],
       ...,
       [0.14285714, 0.21086262, 0.03618687, ..., 0.16129032, 0.09090909,
        1.        ],
       [0.07142857, 0.2172524 , 0.03934189, ..., 0.        , 0.63636364,
        1.        ],
       [0.07142857, 0.23961661, 0.04037019, ..., 0.        , 1.        ,
        0.        ]])

In [29]:
train_Y_scaled

array([[0.24107763],
       [0.20358284],
       [0.26190807],
       ...,
       [0.321622  ],
       [0.14890293],
       [0.15636717]])

In [30]:
print(train_X_scaled.shape)
print(train_Y_scaled.shape)

(1460, 58)
(1460, 1)


In [31]:
import numpy as np
total_data = np.append(train_X_scaled, train_Y_scaled, axis = 1)

In [32]:
print(total_data.shape)

(1460, 59)


In [33]:
from sklearn.model_selection import train_test_split
(train, test) = train_test_split(total_data, test_size=0.25, random_state=42)

In [34]:
trainX = train[:,:58]
trainY = train[:,-1]
testX = test[:,:58]
testY = test[:,-1]
print(trainX.shape)
print(trainY.shape)

(1095, 58)
(1095,)


In [35]:
train_Y_scaled

array([[0.24107763],
       [0.20358284],
       [0.26190807],
       ...,
       [0.321622  ],
       [0.14890293],
       [0.15636717]])

In [36]:
trainY = trainY.reshape((trainY.shape[0],1))
print(trainY.shape)

(1095, 1)


In [37]:
testY = testY.reshape((testY.shape[0],1))

## 2 hidden layers, 100 epochs, time taken = 23s

In [40]:
start = time.time()
m = multiple.Multiple_Model_Gen_V2(trainX, trainY, testX, testY, 100, 128, input_shape = 58, max_no_layers = 2, model_per_batch = 10)
m.get_model_confs()
m.train_models()
end = time.time()
print("Time Taken : ", (end-start))

36
[['', 58, 2, 'relu', {'layer1': 16, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 128}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 196}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 256}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 128}, [1, None]]]
[['', 58, 2, 'relu', {'layer1': 32, 'layer2': 196}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 256}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 128}, [1, None

Epoch 1/100
9/9 [==============================] - 1s 4ms/step - loss: 2.2302 - output_layer_dense_16_16_loss: 0.2835 - output_layer_dense_16_32_loss: 0.2525 - output_layer_dense_16_64_loss: 0.1085 - output_layer_dense_16_128_loss: 0.2951 - output_layer_dense_16_196_loss: 0.1564 - output_layer_dense_16_256_loss: 0.1601 - output_layer_dense_32_16_loss: 0.2217 - output_layer_dense_32_32_loss: 0.3118 - output_layer_dense_32_64_loss: 0.3234 - output_layer_dense_32_128_loss: 0.1171
Epoch 2/100
9/9 [==============================] - 0s 4ms/step - loss: 1.2332 - output_layer_dense_16_16_loss: 0.1463 - output_layer_dense_16_32_loss: 0.1260 - output_layer_dense_16_64_loss: 0.0896 - output_layer_dense_16_128_loss: 0.1311 - output_layer_dense_16_196_loss: 0.1002 - output_layer_dense_16_256_loss: 0.1005 - output_layer_dense_32_16_loss: 0.1392 - output_layer_dense_32_32_loss: 0.1501 - output_layer_dense_32_64_loss: 0.1589 - output_layer_dense_32_128_loss: 0.0912
Epoch 3/100
9/9 [===================

9/9 [==============================] - 0s 4ms/step - loss: 0.4905 - output_layer_dense_16_16_loss: 0.0569 - output_layer_dense_16_32_loss: 0.0526 - output_layer_dense_16_64_loss: 0.0487 - output_layer_dense_16_128_loss: 0.0546 - output_layer_dense_16_196_loss: 0.0446 - output_layer_dense_16_256_loss: 0.0466 - output_layer_dense_32_16_loss: 0.0487 - output_layer_dense_32_32_loss: 0.0439 - output_layer_dense_32_64_loss: 0.0525 - output_layer_dense_32_128_loss: 0.0413
Epoch 18/100
9/9 [==============================] - 0s 4ms/step - loss: 0.4683 - output_layer_dense_16_16_loss: 0.0540 - output_layer_dense_16_32_loss: 0.0501 - output_layer_dense_16_64_loss: 0.0468 - output_layer_dense_16_128_loss: 0.0537 - output_layer_dense_16_196_loss: 0.0416 - output_layer_dense_16_256_loss: 0.0456 - output_layer_dense_32_16_loss: 0.0460 - output_layer_dense_32_32_loss: 0.0428 - output_layer_dense_32_64_loss: 0.0500 - output_layer_dense_32_128_loss: 0.0377
Epoch 19/100
9/9 [=============================

9/9 [==============================] - 0s 4ms/step - loss: 0.3528 - output_layer_dense_16_16_loss: 0.0411 - output_layer_dense_16_32_loss: 0.0374 - output_layer_dense_16_64_loss: 0.0375 - output_layer_dense_16_128_loss: 0.0401 - output_layer_dense_16_196_loss: 0.0337 - output_layer_dense_16_256_loss: 0.0335 - output_layer_dense_32_16_loss: 0.0349 - output_layer_dense_32_32_loss: 0.0324 - output_layer_dense_32_64_loss: 0.0351 - output_layer_dense_32_128_loss: 0.0271
Epoch 34/100
9/9 [==============================] - 0s 4ms/step - loss: 0.3960 - output_layer_dense_16_16_loss: 0.0464 - output_layer_dense_16_32_loss: 0.0442 - output_layer_dense_16_64_loss: 0.0418 - output_layer_dense_16_128_loss: 0.0460 - output_layer_dense_16_196_loss: 0.0359 - output_layer_dense_16_256_loss: 0.0387 - output_layer_dense_32_16_loss: 0.0371 - output_layer_dense_32_32_loss: 0.0354 - output_layer_dense_32_64_loss: 0.0406 - output_layer_dense_32_128_loss: 0.0298
Epoch 35/100
9/9 [=============================

9/9 [==============================] - 0s 4ms/step - loss: 0.2909 - output_layer_dense_16_16_loss: 0.0345 - output_layer_dense_16_32_loss: 0.0326 - output_layer_dense_16_64_loss: 0.0306 - output_layer_dense_16_128_loss: 0.0320 - output_layer_dense_16_196_loss: 0.0266 - output_layer_dense_16_256_loss: 0.0277 - output_layer_dense_32_16_loss: 0.0293 - output_layer_dense_32_32_loss: 0.0285 - output_layer_dense_32_64_loss: 0.0281 - output_layer_dense_32_128_loss: 0.0208
Epoch 50/100
9/9 [==============================] - 0s 4ms/step - loss: 0.3381 - output_layer_dense_16_16_loss: 0.0396 - output_layer_dense_16_32_loss: 0.0393 - output_layer_dense_16_64_loss: 0.0389 - output_layer_dense_16_128_loss: 0.0401 - output_layer_dense_16_196_loss: 0.0290 - output_layer_dense_16_256_loss: 0.0314 - output_layer_dense_32_16_loss: 0.0319 - output_layer_dense_32_32_loss: 0.0298 - output_layer_dense_32_64_loss: 0.0328 - output_layer_dense_32_128_loss: 0.0252
Epoch 51/100
9/9 [=============================

...

9/9 [==============================] - 0s 4ms/step - loss: 0.1061 - output_layer_dense_128_64_loss: 0.0070 - output_layer_dense_128_128_loss: 0.0096 - output_layer_dense_128_196_loss: 0.0093 - output_layer_dense_128_256_loss: 0.0073 - output_layer_dense_196_16_loss: 0.0148 - output_layer_dense_196_32_loss: 0.0081 - output_layer_dense_196_64_loss: 0.0203 - output_layer_dense_196_128_loss: 0.0103 - output_layer_dense_196_196_loss: 0.0074 - output_layer_dense_196_256_loss: 0.0120
Epoch 98/100
9/9 [==============================] - 0s 4ms/step - loss: 0.1004 - output_layer_dense_128_64_loss: 0.0064 - output_layer_dense_128_128_loss: 0.0082 - output_layer_dense_128_196_loss: 0.0094 - output_layer_dense_128_256_loss: 0.0080 - output_layer_dense_196_16_loss: 0.0123 - output_layer_dense_196_32_loss: 0.0110 - output_layer_dense_196_64_loss: 0.0179 - output_layer_dense_196_128_loss: 0.0121 - output_layer_dense_196_196_loss: 0.0068 - output_layer_dense_196_256_loss: 0.0085
Epoch 99/100
9/9 [=====

9/9 [==============================] - 1s 3ms/step - loss: 1.1959 - output_layer_dense_256_16_loss: 0.1411 - output_layer_dense_256_32_loss: 0.3505 - output_layer_dense_256_64_loss: 0.2155 - output_layer_dense_256_128_loss: 0.1682 - output_layer_dense_256_196_loss: 0.1403 - output_layer_dense_256_256_loss: 0.1803
Epoch 2/100
9/9 [==============================] - 0s 3ms/step - loss: 0.4953 - output_layer_dense_256_16_loss: 0.0717 - output_layer_dense_256_32_loss: 0.1034 - output_layer_dense_256_64_loss: 0.0916 - output_layer_dense_256_128_loss: 0.0762 - output_layer_dense_256_196_loss: 0.0798 - output_layer_dense_256_256_loss: 0.0725
Epoch 3/100
9/9 [==============================] - 0s 3ms/step - loss: 0.3762 - output_layer_dense_256_16_loss: 0.0574 - output_layer_dense_256_32_loss: 0.0690 - output_layer_dense_256_64_loss: 0.0690 - output_layer_dense_256_128_loss: 0.0646 - output_layer_dense_256_196_loss: 0.0629 - output_layer_dense_256_256_loss: 0.0533
Epoch 4/100
9/9 [==============

9/9 [==============================] - 0s 3ms/step - loss: 0.1088 - output_layer_dense_256_16_loss: 0.0199 - output_layer_dense_256_32_loss: 0.0222 - output_layer_dense_256_64_loss: 0.0175 - output_layer_dense_256_128_loss: 0.0140 - output_layer_dense_256_196_loss: 0.0185 - output_layer_dense_256_256_loss: 0.0168
Epoch 27/100
9/9 [==============================] - 0s 3ms/step - loss: 0.1140 - output_layer_dense_256_16_loss: 0.0222 - output_layer_dense_256_32_loss: 0.0211 - output_layer_dense_256_64_loss: 0.0183 - output_layer_dense_256_128_loss: 0.0143 - output_layer_dense_256_196_loss: 0.0169 - output_layer_dense_256_256_loss: 0.0212
Epoch 28/100
9/9 [==============================] - 0s 3ms/step - loss: 0.1285 - output_layer_dense_256_16_loss: 0.0263 - output_layer_dense_256_32_loss: 0.0200 - output_layer_dense_256_64_loss: 0.0203 - output_layer_dense_256_128_loss: 0.0146 - output_layer_dense_256_196_loss: 0.0233 - output_layer_dense_256_256_loss: 0.0240
Epoch 29/100
9/9 [===========

9/9 [==============================] - 0s 3ms/step - loss: 0.0691 - output_layer_dense_256_16_loss: 0.0120 - output_layer_dense_256_32_loss: 0.0131 - output_layer_dense_256_64_loss: 0.0109 - output_layer_dense_256_128_loss: 0.0079 - output_layer_dense_256_196_loss: 0.0140 - output_layer_dense_256_256_loss: 0.0112
Epoch 52/100
9/9 [==============================] - 0s 3ms/step - loss: 0.0690 - output_layer_dense_256_16_loss: 0.0107 - output_layer_dense_256_32_loss: 0.0147 - output_layer_dense_256_64_loss: 0.0103 - output_layer_dense_256_128_loss: 0.0079 - output_layer_dense_256_196_loss: 0.0160 - output_layer_dense_256_256_loss: 0.0094
Epoch 53/100
9/9 [==============================] - 0s 3ms/step - loss: 0.0701 - output_layer_dense_256_16_loss: 0.0111 - output_layer_dense_256_32_loss: 0.0164 - output_layer_dense_256_64_loss: 0.0102 - output_layer_dense_256_128_loss: 0.0096 - output_layer_dense_256_196_loss: 0.0117 - output_layer_dense_256_256_loss: 0.0111
Epoch 54/100
9/9 [===========

9/9 [==============================] - 0s 3ms/step - loss: 0.0517 - output_layer_dense_256_16_loss: 0.0085 - output_layer_dense_256_32_loss: 0.0106 - output_layer_dense_256_64_loss: 0.0088 - output_layer_dense_256_128_loss: 0.0091 - output_layer_dense_256_196_loss: 0.0074 - output_layer_dense_256_256_loss: 0.0073
Epoch 77/100
9/9 [==============================] - 0s 3ms/step - loss: 0.0568 - output_layer_dense_256_16_loss: 0.0094 - output_layer_dense_256_32_loss: 0.0124 - output_layer_dense_256_64_loss: 0.0071 - output_layer_dense_256_128_loss: 0.0114 - output_layer_dense_256_196_loss: 0.0072 - output_layer_dense_256_256_loss: 0.0092
Epoch 78/100
9/9 [==============================] - 0s 3ms/step - loss: 0.0545 - output_layer_dense_256_16_loss: 0.0137 - output_layer_dense_256_32_loss: 0.0113 - output_layer_dense_256_64_loss: 0.0070 - output_layer_dense_256_128_loss: 0.0075 - output_layer_dense_256_196_loss: 0.0070 - output_layer_dense_256_256_loss: 0.0081
Epoch 79/100
9/9 [===========

In [41]:
m.evaluate_dict_list

[{'model_name': 'dense_128_64',
  'score': 0.005797526333481073,
  'path_weights': 'dense_128_64',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f25804b3e80>},
 {'model_name': 'dense_128_196',
  'score': 0.0059461272321641445,
  'path_weights': 'dense_128_196',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f258057da00>},
 {'model_name': 'dense_64_256',
  'score': 0.006228855345398188,
  'path_weights': 'dense_64_256',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f25804f6df0>},
 {'model_name': 'dense_196_128',
  'score': 0.006264399271458387,
  'path_weights': 'dense_196_128',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f258057d910>},
 {'model_name': 'dense_256_16',
  'score': 0.006325442809611559,
  'path_weights': 'dense_256_16',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f258077c2e0>},
 {'model_name': 'dense_256_128',
  'score': 0.006332273595035076,
  'p

## 2,3 Hidden Layers, 100 epochs, time taken = 147s (model saved)

In [52]:
start = time.time()
m = multiple.Multiple_Model_Gen_V2(trainX, trainY, testX, testY, 100, 128, input_shape = 58, 
                                   max_no_layers = 3, model_per_batch = 10, 
                                   save_dir = "/home/anish/ASC_ML_test_weights/")
m.get_model_confs()
m.train_models()
end = time.time()
print("Time Taken : ", (end-start))

197
[['', 58, 2, 'relu', {'layer1': 16, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 128}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 196}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 256}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 128}, [1, None]]]
[['', 58, 2, 'relu', {'layer1': 32, 'layer2': 196}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 256}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 128}, [1, Non

Epoch 1/100
9/9 [==============================] - 1s 4ms/step - loss: 2.8549 - output_layer_dense_16_16_loss: 0.2654 - output_layer_dense_16_32_loss: 0.6897 - output_layer_dense_16_64_loss: 0.2600 - output_layer_dense_16_128_loss: 0.1839 - output_layer_dense_16_196_loss: 0.1459 - output_layer_dense_16_256_loss: 0.1763 - output_layer_dense_32_16_loss: 0.2361 - output_layer_dense_32_32_loss: 0.4321 - output_layer_dense_32_64_loss: 0.3570 - output_layer_dense_32_128_loss: 0.1085
Epoch 2/100
9/9 [==============================] - 0s 4ms/step - loss: 1.5609 - output_layer_dense_16_16_loss: 0.1368 - output_layer_dense_16_32_loss: 0.4147 - output_layer_dense_16_64_loss: 0.1138 - output_layer_dense_16_128_loss: 0.1268 - output_layer_dense_16_196_loss: 0.1108 - output_layer_dense_16_256_loss: 0.1095 - output_layer_dense_32_16_loss: 0.1398 - output_layer_dense_32_32_loss: 0.1636 - output_layer_dense_32_64_loss: 0.1580 - output_layer_dense_32_128_loss: 0.0870
Epoch 3/100
9/9 [===================

9/9 [==============================] - 0s 4ms/step - loss: 0.4906 - output_layer_dense_16_16_loss: 0.0532 - output_layer_dense_16_32_loss: 0.0580 - output_layer_dense_16_64_loss: 0.0477 - output_layer_dense_16_128_loss: 0.0495 - output_layer_dense_16_196_loss: 0.0487 - output_layer_dense_16_256_loss: 0.0464 - output_layer_dense_32_16_loss: 0.0485 - output_layer_dense_32_32_loss: 0.0508 - output_layer_dense_32_64_loss: 0.0460 - output_layer_dense_32_128_loss: 0.0418
Epoch 18/100
9/9 [==============================] - 0s 5ms/step - loss: 0.5253 - output_layer_dense_16_16_loss: 0.0563 - output_layer_dense_16_32_loss: 0.0618 - output_layer_dense_16_64_loss: 0.0507 - output_layer_dense_16_128_loss: 0.0553 - output_layer_dense_16_196_loss: 0.0522 - output_layer_dense_16_256_loss: 0.0483 - output_layer_dense_32_16_loss: 0.0512 - output_layer_dense_32_32_loss: 0.0534 - output_layer_dense_32_64_loss: 0.0499 - output_layer_dense_32_128_loss: 0.0462
Epoch 19/100
9/9 [=============================

9/9 [==============================] - 0s 4ms/step - loss: 0.3923 - output_layer_dense_16_16_loss: 0.0427 - output_layer_dense_16_32_loss: 0.0495 - output_layer_dense_16_64_loss: 0.0397 - output_layer_dense_16_128_loss: 0.0402 - output_layer_dense_16_196_loss: 0.0411 - output_layer_dense_16_256_loss: 0.0314 - output_layer_dense_32_16_loss: 0.0389 - output_layer_dense_32_32_loss: 0.0399 - output_layer_dense_32_64_loss: 0.0358 - output_layer_dense_32_128_loss: 0.0330
Epoch 34/100
9/9 [==============================] - 0s 4ms/step - loss: 0.3820 - output_layer_dense_16_16_loss: 0.0423 - output_layer_dense_16_32_loss: 0.0480 - output_layer_dense_16_64_loss: 0.0386 - output_layer_dense_16_128_loss: 0.0382 - output_layer_dense_16_196_loss: 0.0385 - output_layer_dense_16_256_loss: 0.0316 - output_layer_dense_32_16_loss: 0.0388 - output_layer_dense_32_32_loss: 0.0383 - output_layer_dense_32_64_loss: 0.0353 - output_layer_dense_32_128_loss: 0.0325
Epoch 35/100
9/9 [=============================

9/9 [==============================] - 0s 4ms/step - loss: 0.3108 - output_layer_dense_16_16_loss: 0.0347 - output_layer_dense_16_32_loss: 0.0378 - output_layer_dense_16_64_loss: 0.0321 - output_layer_dense_16_128_loss: 0.0316 - output_layer_dense_16_196_loss: 0.0333 - output_layer_dense_16_256_loss: 0.0246 - output_layer_dense_32_16_loss: 0.0325 - output_layer_dense_32_32_loss: 0.0295 - output_layer_dense_32_64_loss: 0.0281 - output_layer_dense_32_128_loss: 0.0266
Epoch 50/100
9/9 [==============================] - 0s 4ms/step - loss: 0.3218 - output_layer_dense_16_16_loss: 0.0350 - output_layer_dense_16_32_loss: 0.0410 - output_layer_dense_16_64_loss: 0.0324 - output_layer_dense_16_128_loss: 0.0373 - output_layer_dense_16_196_loss: 0.0359 - output_layer_dense_16_256_loss: 0.0237 - output_layer_dense_32_16_loss: 0.0320 - output_layer_dense_32_32_loss: 0.0298 - output_layer_dense_32_64_loss: 0.0277 - output_layer_dense_32_128_loss: 0.0270
Epoch 51/100
9/9 [=============================

...

9/9 [==============================] - 0s 5ms/step - loss: 0.1078 - output_layer_dense_256_196_16_loss: 0.0118 - output_layer_dense_256_196_32_loss: 0.0120 - output_layer_dense_256_196_64_loss: 0.0086 - output_layer_dense_256_196_128_loss: 0.0118 - output_layer_dense_256_196_196_loss: 0.0096 - output_layer_dense_256_256_16_loss: 0.0126 - output_layer_dense_256_256_32_loss: 0.0119 - output_layer_dense_256_256_64_loss: 0.0086 - output_layer_dense_256_256_128_loss: 0.0105 - output_layer_dense_256_256_196_loss: 0.0105
Epoch 47/100
9/9 [==============================] - 0s 5ms/step - loss: 0.1055 - output_layer_dense_256_196_16_loss: 0.0126 - output_layer_dense_256_196_32_loss: 0.0087 - output_layer_dense_256_196_64_loss: 0.0082 - output_layer_dense_256_196_128_loss: 0.0107 - output_layer_dense_256_196_196_loss: 0.0153 - output_layer_dense_256_256_16_loss: 0.0129 - output_layer_dense_256_256_32_loss: 0.0085 - output_layer_dense_256_256_64_loss: 0.0115 - output_layer_dense_256_256_128_loss: 

9/9 [==============================] - 0s 5ms/step - loss: 0.0879 - output_layer_dense_256_196_16_loss: 0.0071 - output_layer_dense_256_196_32_loss: 0.0104 - output_layer_dense_256_196_64_loss: 0.0108 - output_layer_dense_256_196_128_loss: 0.0092 - output_layer_dense_256_196_196_loss: 0.0116 - output_layer_dense_256_256_16_loss: 0.0082 - output_layer_dense_256_256_32_loss: 0.0087 - output_layer_dense_256_256_64_loss: 0.0086 - output_layer_dense_256_256_128_loss: 0.0076 - output_layer_dense_256_256_196_loss: 0.0057
Epoch 62/100
9/9 [==============================] - 0s 5ms/step - loss: 0.0877 - output_layer_dense_256_196_16_loss: 0.0077 - output_layer_dense_256_196_32_loss: 0.0104 - output_layer_dense_256_196_64_loss: 0.0115 - output_layer_dense_256_196_128_loss: 0.0083 - output_layer_dense_256_196_196_loss: 0.0084 - output_layer_dense_256_256_16_loss: 0.0082 - output_layer_dense_256_256_32_loss: 0.0097 - output_layer_dense_256_256_64_loss: 0.0076 - output_layer_dense_256_256_128_loss: 

9/9 [==============================] - 0s 5ms/step - loss: 0.0870 - output_layer_dense_256_196_16_loss: 0.0063 - output_layer_dense_256_196_32_loss: 0.0097 - output_layer_dense_256_196_64_loss: 0.0071 - output_layer_dense_256_196_128_loss: 0.0064 - output_layer_dense_256_196_196_loss: 0.0087 - output_layer_dense_256_256_16_loss: 0.0069 - output_layer_dense_256_256_32_loss: 0.0104 - output_layer_dense_256_256_64_loss: 0.0132 - output_layer_dense_256_256_128_loss: 0.0101 - output_layer_dense_256_256_196_loss: 0.0082
Epoch 77/100
9/9 [==============================] - 0s 5ms/step - loss: 0.0893 - output_layer_dense_256_196_16_loss: 0.0065 - output_layer_dense_256_196_32_loss: 0.0117 - output_layer_dense_256_196_64_loss: 0.0107 - output_layer_dense_256_196_128_loss: 0.0063 - output_layer_dense_256_196_196_loss: 0.0111 - output_layer_dense_256_256_16_loss: 0.0090 - output_layer_dense_256_256_32_loss: 0.0077 - output_layer_dense_256_256_64_loss: 0.0111 - output_layer_dense_256_256_128_loss: 

9/9 [==============================] - 0s 5ms/step - loss: 0.0761 - output_layer_dense_256_196_16_loss: 0.0103 - output_layer_dense_256_196_32_loss: 0.0051 - output_layer_dense_256_196_64_loss: 0.0065 - output_layer_dense_256_196_128_loss: 0.0078 - output_layer_dense_256_196_196_loss: 0.0072 - output_layer_dense_256_256_16_loss: 0.0059 - output_layer_dense_256_256_32_loss: 0.0082 - output_layer_dense_256_256_64_loss: 0.0093 - output_layer_dense_256_256_128_loss: 0.0075 - output_layer_dense_256_256_196_loss: 0.0084
Epoch 92/100
9/9 [==============================] - 0s 5ms/step - loss: 0.0689 - output_layer_dense_256_196_16_loss: 0.0076 - output_layer_dense_256_196_32_loss: 0.0049 - output_layer_dense_256_196_64_loss: 0.0078 - output_layer_dense_256_196_128_loss: 0.0079 - output_layer_dense_256_196_196_loss: 0.0072 - output_layer_dense_256_256_16_loss: 0.0075 - output_layer_dense_256_256_32_loss: 0.0060 - output_layer_dense_256_256_64_loss: 0.0059 - output_layer_dense_256_256_128_loss: 

9/9 [==============================] - 0s 1ms/step - loss: 0.0242
Epoch 13/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0253
Epoch 14/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0213
Epoch 15/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0195
Epoch 16/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0207
Epoch 17/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0169
Epoch 18/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0189
Epoch 19/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0148
Epoch 20/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0144
Epoch 21/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0197
Epoch 22/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0219
Epoch 23/100
9/9 [==============================] - 0s 1ms/step - loss: 0.0193
Epoch 24/100
9/9 [==============================] - 0s 1ms/step -

In [53]:
m.evaluate_dict_list

[{'model_name': 'dense_128_128_64',
  'score': 0.004682077094912529,
  'path_weights': '/home/anish/ASC_ML_test_weights/dense_128_128_64',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f24f4d774c0>},
 {'model_name': 'dense_196_256_16',
  'score': 0.00477315578609705,
  'path_weights': '/home/anish/ASC_ML_test_weights/dense_196_256_16',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f237c1f26a0>},
 {'model_name': 'dense_64_256_256',
  'score': 0.0047886730171740055,
  'path_weights': '/home/anish/ASC_ML_test_weights/dense_64_256_256',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f24e44f9f70>},
 {'model_name': 'dense_64_64_128',
  'score': 0.004861713852733374,
  'path_weights': '/home/anish/ASC_ML_test_weights/dense_64_64_128',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f24f4de9ee0>},
 {'model_name': 'dense_256_256_64',
  'score': 0.004981555975973606,
  'path_weights': '/home/anish/AS

## 2,3 Hidden Layers, 25 epochs, time taken = 77s

In [47]:
start = time.time()
m = multiple.Multiple_Model_Gen_V2(trainX, trainY, testX, testY, 25, 128, input_shape = 58, max_no_layers = 3, model_per_batch = 10)
m.get_model_confs()
m.train_models()
end = time.time()
print("Time Taken : ", (end-start))

197
[['', 58, 2, 'relu', {'layer1': 16, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 128}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 196}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 256}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 128}, [1, None]]]
[['', 58, 2, 'relu', {'layer1': 32, 'layer2': 196}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 256}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 128}, [1, Non

Epoch 1/25
9/9 [==============================] - 2s 4ms/step - loss: 2.4979 - output_layer_dense_16_16_loss: 0.1279 - output_layer_dense_16_32_loss: 0.4253 - output_layer_dense_16_64_loss: 0.1376 - output_layer_dense_16_128_loss: 0.1628 - output_layer_dense_16_196_loss: 0.2147 - output_layer_dense_16_256_loss: 0.2348 - output_layer_dense_32_16_loss: 0.3592 - output_layer_dense_32_32_loss: 0.3218 - output_layer_dense_32_64_loss: 0.4098 - output_layer_dense_32_128_loss: 0.1041
Epoch 2/25
9/9 [==============================] - 0s 4ms/step - loss: 1.2861 - output_layer_dense_16_16_loss: 0.1085 - output_layer_dense_16_32_loss: 0.1651 - output_layer_dense_16_64_loss: 0.0984 - output_layer_dense_16_128_loss: 0.1064 - output_layer_dense_16_196_loss: 0.1189 - output_layer_dense_16_256_loss: 0.1309 - output_layer_dense_32_16_loss: 0.1578 - output_layer_dense_32_32_loss: 0.1318 - output_layer_dense_32_64_loss: 0.1864 - output_layer_dense_32_128_loss: 0.0819
Epoch 3/25
9/9 [======================

9/9 [==============================] - 0s 4ms/step - loss: 0.4956 - output_layer_dense_16_16_loss: 0.0547 - output_layer_dense_16_32_loss: 0.0563 - output_layer_dense_16_64_loss: 0.0466 - output_layer_dense_16_128_loss: 0.0499 - output_layer_dense_16_196_loss: 0.0503 - output_layer_dense_16_256_loss: 0.0435 - output_layer_dense_32_16_loss: 0.0537 - output_layer_dense_32_32_loss: 0.0477 - output_layer_dense_32_64_loss: 0.0510 - output_layer_dense_32_128_loss: 0.0418
Epoch 19/25
9/9 [==============================] - 0s 4ms/step - loss: 0.5090 - output_layer_dense_16_16_loss: 0.0561 - output_layer_dense_16_32_loss: 0.0595 - output_layer_dense_16_64_loss: 0.0481 - output_layer_dense_16_128_loss: 0.0512 - output_layer_dense_16_196_loss: 0.0527 - output_layer_dense_16_256_loss: 0.0430 - output_layer_dense_32_16_loss: 0.0535 - output_layer_dense_32_32_loss: 0.0499 - output_layer_dense_32_64_loss: 0.0522 - output_layer_dense_32_128_loss: 0.0429
Epoch 20/25
9/9 [==============================]

Epoch 1/25
9/9 [==============================] - 1s 4ms/step - loss: 2.0044 - output_layer_dense_32_196_loss: 0.2137 - output_layer_dense_32_256_loss: 0.1983 - output_layer_dense_64_16_loss: 0.1377 - output_layer_dense_64_32_loss: 0.2160 - output_layer_dense_64_64_loss: 0.1171 - output_layer_dense_64_128_loss: 0.3075 - output_layer_dense_64_196_loss: 0.0983 - output_layer_dense_64_256_loss: 0.2040 - output_layer_dense_128_16_loss: 0.1823 - output_layer_dense_128_32_loss: 0.3297
Epoch 2/25
9/9 [==============================] - 0s 4ms/step - loss: 0.9523 - output_layer_dense_32_196_loss: 0.0929 - output_layer_dense_32_256_loss: 0.0946 - output_layer_dense_64_16_loss: 0.0894 - output_layer_dense_64_32_loss: 0.1002 - output_layer_dense_64_64_loss: 0.0757 - output_layer_dense_64_128_loss: 0.1422 - output_layer_dense_64_196_loss: 0.0618 - output_layer_dense_64_256_loss: 0.0828 - output_layer_dense_128_16_loss: 0.0969 - output_layer_dense_128_32_loss: 0.1158
Epoch 3/25
9/9 [================

9/9 [==============================] - 0s 4ms/step - loss: 0.3243 - output_layer_dense_32_196_loss: 0.0374 - output_layer_dense_32_256_loss: 0.0323 - output_layer_dense_64_16_loss: 0.0332 - output_layer_dense_64_32_loss: 0.0377 - output_layer_dense_64_64_loss: 0.0334 - output_layer_dense_64_128_loss: 0.0311 - output_layer_dense_64_196_loss: 0.0262 - output_layer_dense_64_256_loss: 0.0310 - output_layer_dense_128_16_loss: 0.0310 - output_layer_dense_128_32_loss: 0.0309
Epoch 18/25
9/9 [==============================] - 0s 4ms/step - loss: 0.3329 - output_layer_dense_32_196_loss: 0.0371 - output_layer_dense_32_256_loss: 0.0329 - output_layer_dense_64_16_loss: 0.0352 - output_layer_dense_64_32_loss: 0.0393 - output_layer_dense_64_64_loss: 0.0346 - output_layer_dense_64_128_loss: 0.0318 - output_layer_dense_64_196_loss: 0.0265 - output_layer_dense_64_256_loss: 0.0310 - output_layer_dense_128_16_loss: 0.0319 - output_layer_dense_128_32_loss: 0.0326
Epoch 19/25
9/9 [=========================

...

9/9 [==============================] - 2s 5ms/step - loss: 1.5807 - output_layer_dense_256_16_16_loss: 0.1072 - output_layer_dense_256_32_16_loss: 0.1940 - output_layer_dense_256_32_32_loss: 0.1666 - output_layer_dense_256_64_16_loss: 0.1918 - output_layer_dense_256_64_32_loss: 0.1113 - output_layer_dense_256_64_64_loss: 0.1560 - output_layer_dense_256_128_16_loss: 0.1654 - output_layer_dense_256_128_32_loss: 0.1159 - output_layer_dense_256_128_64_loss: 0.1651 - output_layer_dense_256_128_128_loss: 0.2073
Epoch 2/25
9/9 [==============================] - 0s 5ms/step - loss: 0.7025 - output_layer_dense_256_16_16_loss: 0.0642 - output_layer_dense_256_32_16_loss: 0.0763 - output_layer_dense_256_32_32_loss: 0.0767 - output_layer_dense_256_64_16_loss: 0.0866 - output_layer_dense_256_64_32_loss: 0.0605 - output_layer_dense_256_64_64_loss: 0.0717 - output_layer_dense_256_128_16_loss: 0.0717 - output_layer_dense_256_128_32_loss: 0.0571 - output_layer_dense_256_128_64_loss: 0.0656 - output_laye

9/9 [==============================] - 0s 5ms/step - loss: 0.2606 - output_layer_dense_256_16_16_loss: 0.0264 - output_layer_dense_256_32_16_loss: 0.0311 - output_layer_dense_256_32_32_loss: 0.0321 - output_layer_dense_256_64_16_loss: 0.0301 - output_layer_dense_256_64_32_loss: 0.0254 - output_layer_dense_256_64_64_loss: 0.0265 - output_layer_dense_256_128_16_loss: 0.0240 - output_layer_dense_256_128_32_loss: 0.0209 - output_layer_dense_256_128_64_loss: 0.0212 - output_layer_dense_256_128_128_loss: 0.0229
Epoch 17/25
9/9 [==============================] - 0s 5ms/step - loss: 0.2623 - output_layer_dense_256_16_16_loss: 0.0260 - output_layer_dense_256_32_16_loss: 0.0328 - output_layer_dense_256_32_32_loss: 0.0306 - output_layer_dense_256_64_16_loss: 0.0304 - output_layer_dense_256_64_32_loss: 0.0258 - output_layer_dense_256_64_64_loss: 0.0281 - output_layer_dense_256_128_16_loss: 0.0257 - output_layer_dense_256_128_32_loss: 0.0203 - output_layer_dense_256_128_64_loss: 0.0203 - output_lay

__________________________________________________________________________________________________
layer2_dense_256_196_196 (Dense (None, 196)          50372       layer1_dense_256_196_196[0][0]   
__________________________________________________________________________________________________
layer2_dense_256_256_16 (Dense) (None, 256)          65792       layer1_dense_256_256_16[0][0]    
__________________________________________________________________________________________________
layer2_dense_256_256_32 (Dense) (None, 256)          65792       layer1_dense_256_256_32[0][0]    
__________________________________________________________________________________________________
layer2_dense_256_256_64 (Dense) (None, 256)          65792       layer1_dense_256_256_64[0][0]    
__________________________________________________________________________________________________
layer2_dense_256_256_128 (Dense (None, 256)          65792       layer1_dense_256_256_128[0][0]   
__________

9/9 [==============================] - 0s 5ms/step - loss: 0.4121 - output_layer_dense_256_196_16_loss: 0.0419 - output_layer_dense_256_196_32_loss: 0.0455 - output_layer_dense_256_196_64_loss: 0.0413 - output_layer_dense_256_196_128_loss: 0.0400 - output_layer_dense_256_196_196_loss: 0.0428 - output_layer_dense_256_256_16_loss: 0.0416 - output_layer_dense_256_256_32_loss: 0.0407 - output_layer_dense_256_256_64_loss: 0.0403 - output_layer_dense_256_256_128_loss: 0.0386 - output_layer_dense_256_256_196_loss: 0.0395
Epoch 7/25
9/9 [==============================] - 0s 5ms/step - loss: 0.3506 - output_layer_dense_256_196_16_loss: 0.0363 - output_layer_dense_256_196_32_loss: 0.0390 - output_layer_dense_256_196_64_loss: 0.0358 - output_layer_dense_256_196_128_loss: 0.0334 - output_layer_dense_256_196_196_loss: 0.0359 - output_layer_dense_256_256_16_loss: 0.0363 - output_layer_dense_256_256_32_loss: 0.0338 - output_layer_dense_256_256_64_loss: 0.0341 - output_layer_dense_256_256_128_loss: 0.

9/9 [==============================] - 0s 5ms/step - loss: 0.1878 - output_layer_dense_256_196_16_loss: 0.0227 - output_layer_dense_256_196_32_loss: 0.0211 - output_layer_dense_256_196_64_loss: 0.0232 - output_layer_dense_256_196_128_loss: 0.0141 - output_layer_dense_256_196_196_loss: 0.0151 - output_layer_dense_256_256_16_loss: 0.0253 - output_layer_dense_256_256_32_loss: 0.0169 - output_layer_dense_256_256_64_loss: 0.0178 - output_layer_dense_256_256_128_loss: 0.0154 - output_layer_dense_256_256_196_loss: 0.0162
Epoch 22/25
9/9 [==============================] - 0s 5ms/step - loss: 0.1819 - output_layer_dense_256_196_16_loss: 0.0240 - output_layer_dense_256_196_32_loss: 0.0212 - output_layer_dense_256_196_64_loss: 0.0199 - output_layer_dense_256_196_128_loss: 0.0146 - output_layer_dense_256_196_196_loss: 0.0148 - output_layer_dense_256_256_16_loss: 0.0211 - output_layer_dense_256_256_32_loss: 0.0179 - output_layer_dense_256_256_64_loss: 0.0177 - output_layer_dense_256_256_128_loss: 0

In [48]:
m.evaluate_dict_list

[{'model_name': 'dense_256_196_128',
  'score': 0.0107438825070858,
  'path_weights': 'dense_256_196_128',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f2588349be0>},
 {'model_name': 'dense_196_256_64',
  'score': 0.011116482317447662,
  'path_weights': 'dense_196_256_64',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f25806887c0>},
 {'model_name': 'dense_196_256_32',
  'score': 0.011166953481733799,
  'path_weights': 'dense_196_256_32',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f25806886a0>},
 {'model_name': 'dense_196_256_256',
  'score': 0.011209127493202686,
  'path_weights': 'dense_196_256_256',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f258067d040>},
 {'model_name': 'dense_196_196_32',
  'score': 0.01169252023100853,
  'path_weights': 'dense_196_196_32',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f255c128c40>},
 {'model_name': 'dense_256_256_128

## 2,3,4 Hidden Layers, 100 epochs, time taken = 767s

In [43]:
start = time.time()
m = multiple.Multiple_Model_Gen_V2(trainX, trainY, testX, testY, 100, 128, input_shape = 58, max_no_layers = 4, model_per_batch = 10)
m.get_model_confs()
m.train_models()
end = time.time()
print("Time Taken : ", (end-start))

833
[['', 58, 2, 'relu', {'layer1': 16, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 128}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 196}, [1, None]], ['', 58, 2, 'relu', {'layer1': 16, 'layer2': 256}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 128}, [1, None]]]
[['', 58, 2, 'relu', {'layer1': 32, 'layer2': 196}, [1, None]], ['', 58, 2, 'relu', {'layer1': 32, 'layer2': 256}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 16}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 32}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 64}, [1, None]], ['', 58, 2, 'relu', {'layer1': 64, 'layer2': 128}, [1, Non

9/9 [==============================] - 1s 4ms/step - loss: 1.8786 - output_layer_dense_16_16_loss: 0.1259 - output_layer_dense_16_32_loss: 0.3083 - output_layer_dense_16_64_loss: 0.1338 - output_layer_dense_16_128_loss: 0.2070 - output_layer_dense_16_196_loss: 0.2022 - output_layer_dense_16_256_loss: 0.1286 - output_layer_dense_32_16_loss: 0.1497 - output_layer_dense_32_32_loss: 0.2338 - output_layer_dense_32_64_loss: 0.2511 - output_layer_dense_32_128_loss: 0.1383
Epoch 2/100
9/9 [==============================] - 0s 4ms/step - loss: 1.1747 - output_layer_dense_16_16_loss: 0.1010 - output_layer_dense_16_32_loss: 0.1907 - output_layer_dense_16_64_loss: 0.0922 - output_layer_dense_16_128_loss: 0.1254 - output_layer_dense_16_196_loss: 0.1197 - output_layer_dense_16_256_loss: 0.0885 - output_layer_dense_32_16_loss: 0.1087 - output_layer_dense_32_32_loss: 0.1266 - output_layer_dense_32_64_loss: 0.1352 - output_layer_dense_32_128_loss: 0.0866
Epoch 3/100
9/9 [==============================]

9/9 [==============================] - 0s 4ms/step - loss: 0.4702 - output_layer_dense_16_16_loss: 0.0519 - output_layer_dense_16_32_loss: 0.0532 - output_layer_dense_16_64_loss: 0.0481 - output_layer_dense_16_128_loss: 0.0486 - output_layer_dense_16_196_loss: 0.0464 - output_layer_dense_16_256_loss: 0.0443 - output_layer_dense_32_16_loss: 0.0458 - output_layer_dense_32_32_loss: 0.0460 - output_layer_dense_32_64_loss: 0.0454 - output_layer_dense_32_128_loss: 0.0406
Epoch 19/100
9/9 [==============================] - 0s 4ms/step - loss: 0.4622 - output_layer_dense_16_16_loss: 0.0509 - output_layer_dense_16_32_loss: 0.0518 - output_layer_dense_16_64_loss: 0.0455 - output_layer_dense_16_128_loss: 0.0486 - output_layer_dense_16_196_loss: 0.0458 - output_layer_dense_16_256_loss: 0.0466 - output_layer_dense_32_16_loss: 0.0442 - output_layer_dense_32_32_loss: 0.0461 - output_layer_dense_32_64_loss: 0.0438 - output_layer_dense_32_128_loss: 0.0389
Epoch 20/100
9/9 [=============================

9/9 [==============================] - 0s 4ms/step - loss: 0.3564 - output_layer_dense_16_16_loss: 0.0406 - output_layer_dense_16_32_loss: 0.0424 - output_layer_dense_16_64_loss: 0.0373 - output_layer_dense_16_128_loss: 0.0379 - output_layer_dense_16_196_loss: 0.0359 - output_layer_dense_16_256_loss: 0.0330 - output_layer_dense_32_16_loss: 0.0347 - output_layer_dense_32_32_loss: 0.0344 - output_layer_dense_32_64_loss: 0.0314 - output_layer_dense_32_128_loss: 0.0289
Epoch 35/100
9/9 [==============================] - 0s 4ms/step - loss: 0.3863 - output_layer_dense_16_16_loss: 0.0419 - output_layer_dense_16_32_loss: 0.0446 - output_layer_dense_16_64_loss: 0.0393 - output_layer_dense_16_128_loss: 0.0392 - output_layer_dense_16_196_loss: 0.0378 - output_layer_dense_16_256_loss: 0.0367 - output_layer_dense_32_16_loss: 0.0375 - output_layer_dense_32_32_loss: 0.0369 - output_layer_dense_32_64_loss: 0.0359 - output_layer_dense_32_128_loss: 0.0364
Epoch 36/100
9/9 [=============================

9/9 [==============================] - 0s 4ms/step - loss: 0.3495 - output_layer_dense_16_16_loss: 0.0410 - output_layer_dense_16_32_loss: 0.0439 - output_layer_dense_16_64_loss: 0.0349 - output_layer_dense_16_128_loss: 0.0362 - output_layer_dense_16_196_loss: 0.0326 - output_layer_dense_16_256_loss: 0.0326 - output_layer_dense_32_16_loss: 0.0357 - output_layer_dense_32_32_loss: 0.0336 - output_layer_dense_32_64_loss: 0.0314 - output_layer_dense_32_128_loss: 0.0277
Epoch 51/100
9/9 [==============================] - 0s 4ms/step - loss: 0.3199 - output_layer_dense_16_16_loss: 0.0374 - output_layer_dense_16_32_loss: 0.0413 - output_layer_dense_16_64_loss: 0.0319 - output_layer_dense_16_128_loss: 0.0324 - output_layer_dense_16_196_loss: 0.0300 - output_layer_dense_16_256_loss: 0.0307 - output_layer_dense_32_16_loss: 0.0329 - output_layer_dense_32_32_loss: 0.0301 - output_layer_dense_32_64_loss: 0.0280 - output_layer_dense_32_128_loss: 0.0251
Epoch 52/100
9/9 [=============================

...

9/9 [==============================] - 2s 5ms/step - loss: 0.9025 - output_layer_dense_256_256_256_16_loss: 0.1663 - output_layer_dense_256_256_256_32_loss: 0.1608 - output_layer_dense_256_256_256_64_loss: 0.1456 - output_layer_dense_256_256_256_128_loss: 0.1338 - output_layer_dense_256_256_256_196_loss: 0.1464 - output_layer_dense_256_256_256_256_loss: 0.1497
Epoch 2/100
9/9 [==============================] - 0s 5ms/step - loss: 0.3905 - output_layer_dense_256_256_256_16_loss: 0.0718 - output_layer_dense_256_256_256_32_loss: 0.0720 - output_layer_dense_256_256_256_64_loss: 0.0641 - output_layer_dense_256_256_256_128_loss: 0.0674 - output_layer_dense_256_256_256_196_loss: 0.0548 - output_layer_dense_256_256_256_256_loss: 0.0604
Epoch 3/100
9/9 [==============================] - 0s 5ms/step - loss: 0.3037 - output_layer_dense_256_256_256_16_loss: 0.0539 - output_layer_dense_256_256_256_32_loss: 0.0509 - output_layer_dense_256_256_256_64_loss: 0.0505 - output_layer_dense_256_256_256_128_

9/9 [==============================] - 0s 5ms/step - loss: 0.1012 - output_layer_dense_256_256_256_16_loss: 0.0157 - output_layer_dense_256_256_256_32_loss: 0.0143 - output_layer_dense_256_256_256_64_loss: 0.0173 - output_layer_dense_256_256_256_128_loss: 0.0181 - output_layer_dense_256_256_256_196_loss: 0.0199 - output_layer_dense_256_256_256_256_loss: 0.0159
Epoch 23/100
9/9 [==============================] - 0s 5ms/step - loss: 0.1019 - output_layer_dense_256_256_256_16_loss: 0.0150 - output_layer_dense_256_256_256_32_loss: 0.0149 - output_layer_dense_256_256_256_64_loss: 0.0182 - output_layer_dense_256_256_256_128_loss: 0.0175 - output_layer_dense_256_256_256_196_loss: 0.0166 - output_layer_dense_256_256_256_256_loss: 0.0197
Epoch 24/100
9/9 [==============================] - 0s 5ms/step - loss: 0.1070 - output_layer_dense_256_256_256_16_loss: 0.0138 - output_layer_dense_256_256_256_32_loss: 0.0177 - output_layer_dense_256_256_256_64_loss: 0.0225 - output_layer_dense_256_256_256_12

9/9 [==============================] - 0s 4ms/step - loss: 0.0633 - output_layer_dense_256_256_256_16_loss: 0.0142 - output_layer_dense_256_256_256_32_loss: 0.0098 - output_layer_dense_256_256_256_64_loss: 0.0090 - output_layer_dense_256_256_256_128_loss: 0.0107 - output_layer_dense_256_256_256_196_loss: 0.0083 - output_layer_dense_256_256_256_256_loss: 0.0113
Epoch 44/100
9/9 [==============================] - 0s 4ms/step - loss: 0.0679 - output_layer_dense_256_256_256_16_loss: 0.0150 - output_layer_dense_256_256_256_32_loss: 0.0100 - output_layer_dense_256_256_256_64_loss: 0.0093 - output_layer_dense_256_256_256_128_loss: 0.0108 - output_layer_dense_256_256_256_196_loss: 0.0092 - output_layer_dense_256_256_256_256_loss: 0.0138
Epoch 45/100
9/9 [==============================] - 0s 5ms/step - loss: 0.0625 - output_layer_dense_256_256_256_16_loss: 0.0139 - output_layer_dense_256_256_256_32_loss: 0.0091 - output_layer_dense_256_256_256_64_loss: 0.0086 - output_layer_dense_256_256_256_12

9/9 [==============================] - 0s 3ms/step - loss: 0.0462 - output_layer_dense_256_256_256_16_loss: 0.0064 - output_layer_dense_256_256_256_32_loss: 0.0088 - output_layer_dense_256_256_256_64_loss: 0.0085 - output_layer_dense_256_256_256_128_loss: 0.0073 - output_layer_dense_256_256_256_196_loss: 0.0072 - output_layer_dense_256_256_256_256_loss: 0.0081
Epoch 65/100
9/9 [==============================] - 0s 3ms/step - loss: 0.0447 - output_layer_dense_256_256_256_16_loss: 0.0064 - output_layer_dense_256_256_256_32_loss: 0.0075 - output_layer_dense_256_256_256_64_loss: 0.0070 - output_layer_dense_256_256_256_128_loss: 0.0072 - output_layer_dense_256_256_256_196_loss: 0.0068 - output_layer_dense_256_256_256_256_loss: 0.0097
Epoch 66/100
9/9 [==============================] - 0s 4ms/step - loss: 0.0452 - output_layer_dense_256_256_256_16_loss: 0.0068 - output_layer_dense_256_256_256_32_loss: 0.0055 - output_layer_dense_256_256_256_64_loss: 0.0069 - output_layer_dense_256_256_256_12

9/9 [==============================] - 0s 3ms/step - loss: 0.0468 - output_layer_dense_256_256_256_16_loss: 0.0067 - output_layer_dense_256_256_256_32_loss: 0.0069 - output_layer_dense_256_256_256_64_loss: 0.0057 - output_layer_dense_256_256_256_128_loss: 0.0080 - output_layer_dense_256_256_256_196_loss: 0.0122 - output_layer_dense_256_256_256_256_loss: 0.0074
Epoch 86/100
9/9 [==============================] - 0s 3ms/step - loss: 0.0514 - output_layer_dense_256_256_256_16_loss: 0.0075 - output_layer_dense_256_256_256_32_loss: 0.0090 - output_layer_dense_256_256_256_64_loss: 0.0090 - output_layer_dense_256_256_256_128_loss: 0.0072 - output_layer_dense_256_256_256_196_loss: 0.0098 - output_layer_dense_256_256_256_256_loss: 0.0089
Epoch 87/100
9/9 [==============================] - 0s 4ms/step - loss: 0.0471 - output_layer_dense_256_256_256_16_loss: 0.0065 - output_layer_dense_256_256_256_32_loss: 0.0081 - output_layer_dense_256_256_256_64_loss: 0.0093 - output_layer_dense_256_256_256_12

In [44]:
m.evaluate_dict_list

[{'model_name': 'dense_196_256_196_128',
  'score': 0.0038333504926413298,
  'path_weights': 'dense_196_256_196_128',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f2588947cd0>},
 {'model_name': 'dense_64_196_64_64',
  'score': 0.004144536331295967,
  'path_weights': 'dense_64_196_64_64',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f255c63e370>},
 {'model_name': 'dense_128_128_256_16',
  'score': 0.004153947811573744,
  'path_weights': 'dense_128_128_256_16',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f255c568c70>},
 {'model_name': 'dense_256_256_256_196',
  'score': 0.004201287869364023,
  'path_weights': 'dense_256_256_256_196',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f2588839dc0>},
 {'model_name': 'dense_128_256_256_256',
  'score': 0.004301540087908506,
  'path_weights': 'dense_128_256_256_256',
  'model': <tensorflow.python.keras.engine.functional.Functional at 0x7f258863